![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Systemy Dialogowe </h1>
<h2> 8. <i>Parsing semantyczny z wykorzystaniem technik uczenia maszynowego</i>  [laboratoria]</h2> 
<h3> Marek Kubis (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

Parsing semantyczny z wykorzystaniem technik uczenia maszynowego
================================================================

Wprowadzenie
------------
Problem wykrywania slotów i ich wartości w wypowiedziach użytkownika można sformułować jako zadanie
polegające na przewidywaniu dla poszczególnych słów etykiet wskazujących na to czy i do jakiego
slotu dane słowo należy.

> chciałbym zarezerwować stolik na jutro**/day** na godzinę dwunastą**/hour** czterdzieści**/hour** pięć**/hour** na pięć**/size** osób

Granice slotów oznacza się korzystając z wybranego schematu etykietowania.

### Schemat IOB

| Prefix | Znaczenie                  |
|:------:|:---------------------------|
| I      | wnętrze slotu (inside)     |
| O      | poza slotem (outside)      |
| B      | początek slotu (beginning) |

> chciałbym zarezerwować stolik na jutro**/B-day** na godzinę dwunastą**/B-hour** czterdzieści**/I-hour** pięć**/I-hour** na pięć**/B-size** osób

### Schemat IOBES

| Prefix | Znaczenie                  |
|:------:|:---------------------------|
| I      | wnętrze slotu (inside)     |
| O      | poza slotem (outside)      |
| B      | początek slotu (beginning) |
| E      | koniec slotu (ending)      |
| S      | pojedyncze słowo (single)  |

> chciałbym zarezerwować stolik na jutro**/S-day** na godzinę dwunastą**/B-hour** czterdzieści**/I-hour** pięć**/E-hour** na pięć**/S-size** osób

Jeżeli dla tak sformułowanego zadania przygotujemy zbiór danych
złożony z wypowiedzi użytkownika z oznaczonymi slotami (tzw. *zbiór uczący*),
to możemy zastosować techniki (nadzorowanego) uczenia maszynowego w celu zbudowania modelu
annotującego wypowiedzi użytkownika etykietami slotów.

Do zbudowania takiego modelu można wykorzystać między innymi:

 1. warunkowe pola losowe (Lafferty i in.; 2001),

 2. rekurencyjne sieci neuronowe, np. sieci LSTM (Hochreiter i Schmidhuber; 1997),

 3. transformery (Vaswani i in., 2017).

Przykład
--------
Skorzystamy ze zbioru danych przygotowanego przez Schustera (2019).

In [ ]:
!mkdir -p l07
%cd l07
!curl -L -C -  https://fb.me/multilingual_task_oriented_data  -o data.zip
!unzip data.zip
%cd ..

Zbiór ten gromadzi wypowiedzi w trzech językach opisane slotami dla dwunastu ram należących do trzech dziedzin `Alarm`, `Reminder` oraz `Weather`. Dane wczytamy korzystając z biblioteki [conllu](https://pypi.org/project/conllu/).

In [ ]:
from conllu import parse_incr
fields = ['id', 'form', 'frame', 'slot']

def nolabel2o(line, i):
    return 'O' if line[i] == 'NoLabel' else line[i]

with open('l07/en/train-en.conllu') as trainfile:
    trainset = list(parse_incr(trainfile, fields=fields, field_parsers={'slot': nolabel2o}))
with open('l07/en/test-en.conllu') as testfile:
    testset = list(parse_incr(testfile, fields=fields, field_parsers={'slot': nolabel2o}))

Zobaczmy kilka przykładowych wypowiedzi z tego zbioru.

In [ ]:
from tabulate import tabulate
tabulate(trainset[0], tablefmt='html')

In [ ]:
tabulate(trainset[1000], tablefmt='html')

In [ ]:
tabulate(trainset[2000], tablefmt='html')

Na potrzeby prezentacji procesu uczenia w jupyterowym notatniku zawęzimy zbiór danych do początkowych przykładów.

In [ ]:
trainset = trainset[:100]
testset = testset[:100]

Budując model skorzystamy z architektury opartej o rekurencyjne sieci neuronowe
zaimplementowanej w bibliotece [flair](https://github.com/flairNLP/flair) (Akbik i in. 2018).

In [ ]:
from flair.data import Corpus, Sentence, Token
from flair.datasets import SentenceDataset
from flair.embeddings import StackedEmbeddings
from flair.embeddings import WordEmbeddings
from flair.embeddings import CharacterEmbeddings
from flair.embeddings import FlairEmbeddings
from flair.models import SequenceTagger
from flair.trainers import ModelTrainer

# determinizacja obliczeń
import random
import torch
random.seed(42)
torch.manual_seed(42)

if torch.cuda.is_available():
    torch.cuda.manual_seed(0)
    torch.cuda.manual_seed_all(0)
    torch.backends.cudnn.enabled = False
    torch.backends.cudnn.benchmark = False
    torch.backends.cudnn.deterministic = True

Dane skonwertujemy do formatu wykorzystywanego przez `flair`, korzystając z następującej funkcji.

In [ ]:
def conllu2flair(sentences, label=None):
    fsentences = []

    for sentence in sentences:
        fsentence = Sentence()

        for token in sentence:
            ftoken = Token(token['form'])

            if label:
                ftoken.add_tag(label, token[label])

            fsentence.add_token(ftoken)

        fsentences.append(fsentence)

    return SentenceDataset(fsentences)

corpus = Corpus(train=conllu2flair(trainset, 'slot'), test=conllu2flair(testset, 'slot'))
print(corpus)
tag_dictionary = corpus.make_tag_dictionary(tag_type='slot')
print(tag_dictionary)

Nasz model będzie wykorzystywał wektorowe reprezentacje słów (zob. [Word Embeddings](https://github.com/flairNLP/flair/blob/master/resources/docs/TUTORIAL_3_WORD_EMBEDDING.md)).

In [ ]:
embedding_types = [
    WordEmbeddings('en'),
    FlairEmbeddings('en-forward'),
    FlairEmbeddings('en-backward'),
    CharacterEmbeddings(),
]

embeddings = StackedEmbeddings(embeddings=embedding_types)
tagger = SequenceTagger(hidden_size=256, embeddings=embeddings,
                        tag_dictionary=tag_dictionary,
                        tag_type='slot', use_crf=True)

Zobaczmy jak wygląda architektura sieci neuronowej, która będzie odpowiedzialna za przewidywanie
slotów w wypowiedziach.

In [ ]:
print(tagger)

Wykonamy dziesięć iteracji (epok) uczenia a wynikowy model zapiszemy w katalogu `slot-model`.

In [ ]:
trainer = ModelTrainer(tagger, corpus)
trainer.train('slot-model',
              learning_rate=0.1,
              mini_batch_size=32,
              max_epochs=10,
              train_with_dev=False)

Jakość wyuczonego modelu możemy ocenić, korzystając z zaraportowanych powyżej metryk, tj.:

 - *tp (true positives)*

   > liczba słów oznaczonych w zbiorze testowym etykietą $e$, które model oznaczył tą etykietą

 - *fp (false positives)*

   > liczba słów nieoznaczonych w zbiorze testowym etykietą $e$, które model oznaczył tą etykietą

 - *fn (false negatives)*

   > liczba słów oznaczonych w zbiorze testowym etykietą $e$, którym model nie nadał etykiety $e$

 - *precision*

   > $$\frac{tp}{tp + fp}$$

 - *recall*

   > $$\frac{tp}{tp + fn}$$

 - $F_1$

   > $$\frac{2 \cdot precision \cdot recall}{precision + recall}$$

 - *micro* $F_1$

   > $F_1$ w którym $tp$, $fp$ i $fn$ są liczone łącznie dla wszystkich etykiet, tj. $tp = \sum_{e}{{tp}_e}$, $fn = \sum_{e}{{fn}_e}$, $fp = \sum_{e}{{fp}_e}$

 - *macro* $F_1$

   > średnia arytmetyczna z $F_1$ obliczonych dla poszczególnych etykiet z osobna.

Wyuczony model możemy wczytać z pliku korzystając z metody `load`.

In [ ]:
model = SequenceTagger.load('slot-model/final-model.pt')

Wczytany model możemy wykorzystać do przewidywania slotów w wypowiedziach użytkownika, korzystając
z przedstawionej poniżej funkcji `predict`.

In [ ]:
def predict(model, sentence):
    csentence = [{'form': word} for word in sentence]
    fsentence = conllu2flair([csentence])[0]
    model.predict(fsentence)
    return [(token, ftoken.get_tag('slot').value) for token, ftoken in zip(sentence, fsentence)]


Jak pokazuje przykład poniżej model wyuczony tylko na 100 przykładach popełnia w dosyć prostej
wypowiedzi błąd etykietując słowo `alarm` tagiem `B-weather/noun`.

In [ ]:
tabulate(predict(model, 'change my 3 pm alarm to the next day'.split()), tablefmt='html')

Literatura
----------
 1. Sebastian Schuster, Sonal Gupta, Rushin Shah, Mike Lewis, Cross-lingual Transfer Learning for Multilingual Task Oriented Dialog. NAACL-HLT (1) 2019, pp. 3795-3805
 2. John D. Lafferty, Andrew McCallum, and Fernando C. N. Pereira. 2001. Conditional Random Fields: Probabilistic Models for Segmenting and Labeling Sequence Data. In Proceedings of the Eighteenth International Conference on Machine Learning (ICML '01). Morgan Kaufmann Publishers Inc., San Francisco, CA, USA, 282–289, https://repository.upenn.edu/cgi/viewcontent.cgi?article=1162&context=cis_papers
 3. Sepp Hochreiter and Jürgen Schmidhuber. 1997. Long Short-Term Memory. Neural Comput. 9, 8 (November 15, 1997), 1735–1780, https://doi.org/10.1162/neco.1997.9.8.1735
 4. Ashish Vaswani, Noam Shazeer, Niki Parmar, Jakob Uszkoreit, Llion Jones, Aidan N. Gomez, Lukasz Kaiser, Illia Polosukhin, Attention is All you Need, NIPS 2017, pp. 5998-6008, https://arxiv.org/abs/1706.03762
 5. Alan Akbik, Duncan Blythe, Roland Vollgraf, Contextual String Embeddings for Sequence Labeling, Proceedings of the 27th International Conference on Computational Linguistics, pp. 1638–1649, https://www.aclweb.org/anthology/C18-1139.pdf
